In [1]:
# Install Java 8 (required by Spark)
!apt-get install openjdk-8-jdk-headless -qq > /dev/null

# Download Spark 3.4.1 with Hadoop 3 and extract it
!wget -q https://archivehtbprolapachehtbprolorg-s.evpn.library.nenu.edu.cn/dist/spark/spark-3.4.1/spark-3.4.1-bin-hadoop3.tgz
!tar -xzf spark-3.4.1-bin-hadoop3.tgz

# Install Findspark
!pip install -q findspark


In [2]:
import os

os.environ["JAVA_HOME"] = "/usr/lib/jvm/java-8-openjdk-amd64"
os.environ["SPARK_HOME"] = "/content/spark-3.4.1-bin-hadoop3"


In [3]:
import findspark
findspark.init()

from pyspark.sql import SparkSession

spark = SparkSession.builder.appName("CorruptedRecordsDemo").getOrCreate()
spark


In [ ]:
# Permissive mode

from pyspark.sql.functions import col

customers_schema = '''
customer_id INT,
customer_fname STRING,
customer_lname STRING,
customer_email STRING,
customer_password STRING,
customer_street STRING,
customer_city STRING,
customer_state STRING,
customer_zipcode INT,
_corrupt_record STRING
'''

customers_df = spark.read.schema(customers_schema).format("csv").options(
    header=True,
    delimiter="|",
    mode="PERMISSIVE",
    columnNameOfCorruptRecord="_corrupt_record"
).load("/content/corrupted_customer_details.csv")

customers_df.filter(col("_corrupt_record").isNotNull()).show()
print(f"Total number of records while reading in PERMISSIVE mode: {customers_df.count()}")

In [ ]:
# Dromalformed mode

from pyspark.sql.functions import col

customers_schema = '''
customer_id INT,
customer_fname STRING,
customer_lname STRING,
customer_email STRING,
customer_password STRING,
customer_street STRING,
customer_city STRING,
customer_state STRING,
customer_zipcode INT,
_corrupt_record STRING
'''

customers_df = spark.read.schema(customers_schema).format("csv").options(
    header=True,
    delimiter=",",  # Ensure this matches your CSV
    mode="DROPMALFORMED"  # Drop corrupt rows
).load("/content/corrupted_customer_details.csv")

customers_df.show()
print(f"Total number of records after DROPMALFORMED mode: {customers_df.count()}")

In [7]:
# Failfast mode

from pyspark.sql.functions import col

customers_schema = '''
customer_id INT,
customer_fname STRING,
customer_lname STRING,
customer_email STRING,
customer_password STRING,
customer_street STRING,
customer_city STRING,
customer_state STRING,
customer_zipcode INT,
_corrupt_record STRING
'''
customers_df = spark.read.schema(customers_schema).format("csv").options(
    header=True,
    delimiter=",",  # Ensure this matches your CSV
    mode="FAILFAST"  # Stop on first corrupt record
).load("/content/corrupted_customer_details.csv")

customers_df.show()

Py4JJavaError: An error occurred while calling o83.showString.
: org.apache.spark.SparkException: Job aborted due to stage failure: Task 0 in stage 4.0 failed 1 times, most recent failure: Lost task 0.0 in stage 4.0 (TID 4) (c5570f64142a executor driver): org.apache.spark.SparkException: [MALFORMED_RECORD_IN_PARSING] Malformed records are detected in record parsing: [null,null,null,null,null,null,null,null,null,3|Mark|Brown|mark.brown@email.com|pass789|789 Pine Rd|Chicago|IL|60007].
Parse Mode: FAILFAST. To process malformed records as null result, try setting the option 'mode' as 'PERMISSIVE'.
	at org.apache.spark.sql.errors.QueryExecutionErrors$.malformedRecordsDetectedInRecordParsingError(QueryExecutionErrors.scala:1764)
	at org.apache.spark.sql.catalyst.util.FailureSafeParser.parse(FailureSafeParser.scala:69)
	at org.apache.spark.sql.catalyst.csv.UnivocityParser$.$anonfun$parseIterator$2(UnivocityParser.scala:456)
	at scala.collection.Iterator$$anon$11.nextCur(Iterator.scala:486)
	